In [1]:
from droneinterface import Connection, Vehicle
from pathlib import Path
from flightdata import Flight
from flightanalysis import State, Box

fl = Flight.from_log("/home/td6834/projects/montserrat/BINS/00000032.BIN")
st = State.from_flight(fl, Box.from_initial(fl))

In [2]:
from flightplotting import plotsec
plotsec(st, nmodels=0)

In [5]:
import watch_data
from pathlib import Path
import numpy as np
import pandas as pd
import plotly.graph_objects as go
                            
class Experiment:
    def __init__(self, flight, df, name) -> None:
        self.fl = flight
        self.name = name
        self.df = df
        self.st = State.from_flight(self.fl, Box.from_initial(self.fl))

    @staticmethod
    def from_csv(df: pd.DataFrame, fl: Flight, name):
        return Experiment(
            fl.slice_raw_t(
                slice(
                    df.timestamp.iloc[0], 
                    df.timestamp.iloc[-1], 
                    None
                )
            ),
            df,
            name
        ) 


    def state_trace(self, *args, **kwargs):
        return plotsec(self.st, *args, **kwargs ).data

    def fl_trace(self, y, *args, **kwargs):
        return go.Scatter(x=self.fl.data.index, y=y,*args, **kwargs)


folder = Path("/home/td6834/projects/montserrat/DroneInterfaceOutput/flight_4")
runs = watch_data.get_runs_in_folder(folder)
run = list(runs.values())[0]

results = dict()
for k, p in watch_data.get_recordings_in_folder(run, False).items():
    results[k] = {}
    for csv in sorted(p.glob("*.csv")):
        if not "summary" in csv.name:
            df = pd.read_csv(csv, index_col=0)
            if len(df) > 1:
                results[k][int(csv.stem)] = Experiment.from_csv(df, fl, csv)

In [21]:
from flightdata import Fields
import plotly.express as px

df=results[1][1200].fl.read_fields([Fields.TXCONTROLS, Fields.SERVOS]).loc[:,["tx_controls_7", "servos_8", "servos_9"]]
px.scatter(df)

In [ ]:
#[exp.state_trace() for exp in results[0].values()]
import plotly.express as px


from flightplotting import *
#create_3d_plot([exp.state_trace() for exp in results[0].values()])
fig = go.Figure()

traces = [
#    ("airspeed_0", "y", "dash" ),
    ("current_0", "y", "solid" ),
    ("tx_controls_5", "y1", "solid" )
]


for i, res in enumerate(list(results[3].values())):
    
    color = px.colors.sequential.Viridis[i*2]

    for tr in traces:
        fig.add_trace(res.fl_trace(
            res.fl.data[tr[0]], 
            line=dict(color=color, dash=tr[2]),
            name=f"{tr[0]}_{res.name.stem}",
            yaxis=tr[1]
        ))        

fig
#create_3d_plot(results[0][1200].stat
#e_trace())
#fig

AttributeError: 'DataFrame' object has no attribute 'tx_controls_8'